In [1]:
import pandas as pd
import geopandas as gpd
import folium
import branca.colormap as cm
import matplotlib.pyplot as plt
import branca

In [2]:
berlinhex = gpd.read_file('D:/urbban/berlin_data/berlin_hex2_wgs84.shp')  
berlinhex = gpd.GeoDataFrame(berlinhex,geometry='geometry',crs={'init':'epsg:4326'})


C:\Users\Alex\anaconda3\lib\site-packages\pyproj\crs\crs.py:53: FutureWarning: '+init=<authority>:<code>' syntax is deprecated. '<authority>:<code>' is the preferred initialization method. When making the change, be mindful of axis order changes: https://pyproj4.github.io/pyproj/stable/gotchas.html#axis-order-changes-in-proj-6
  return _prepare_from_string(" ".join(pjargs))


In [3]:
ost = berlinhex['diff_media'].quantile([.16, .33, .50,.66, .83, 1])

In [4]:
berlinhex.diff_media = berlinhex.diff_media.round(1)
ost = berlinhex['diff_media'].quantile([.16, .33, .50,.66, .83, 1])
ost[:1]

0.16     -60.000
0.33     -60.000
0.50      -0.200
0.66      99.580
0.83     321.916
1.00    4075.700
Name: diff_media, dtype: float64

In [5]:
berlinhex2 = berlinhex[berlinhex['diff_media']!= -60]
len(berlinhex2)

1834

In [6]:
x_map=berlinhex.centroid.x.mean()
y_map=berlinhex.centroid.y.mean()
print(x_map,y_map)

13.401113544950114 52.50266692861542


In [7]:
berlinhex2.diff_media.sort_values()

1585     -59.7
1013     -59.6
2387     -59.6
2469     -59.5
2156     -59.2
         ...  
1612    3421.3
1870    3424.9
1753    3462.8
2763    3924.1
1041    4075.7
Name: diff_media, Length: 1834, dtype: float64

In [8]:
berlinone = berlinhex[(berlinhex['diff_media']==-60.0) & (berlinhex['actxhab']== 0) ]
len(berlinone)

1142

## function to erase overlapped choroplet legend

In [9]:
def folium_del_legend(choropleth: folium.Choropleth):
  """A hack to remove choropleth legends.
  
  The choropleth color-scaled legend sometimes looks too crowded. Until there is an
  option to disable the legend, use this routine to remove any color map children
  from the choropleth.
  
  Args:
    choropleth: Choropleth objected created by `folium.Choropleth()`
    
  Returns:
    The same object `choropleth` with any child whose name starts with
    'color_map' removed.
  """
  del_list = []
  for child in choropleth._children:
    if child.startswith('color_map'):
      del_list.append(child)
  for del_item in del_list:
    choropleth._children.pop(del_item)
  return choropleth



In [10]:
mymap = folium.Map(location=[y_map, x_map], zoom_start=11,tiles=None)
folium.TileLayer('CartoDB positron',name="Light Map",control=False).add_to(mymap)

myscale = (berlinhex2['diff_media'].quantile((.0,.16, .33, .50,.66, .83, 1))).tolist()
folium_del_legend(
folium.Choropleth(
 geo_data=berlinhex2,
 name='Economic Activities Coropleth',
 data=berlinhex2,
 columns=['id_hex','diff_media'],
 key_on="feature.properties.id_hex",
 fill_color='RdYlGn_r',
 threshold_scale=myscale,
 fill_opacity=0.6,
 line_opacity=0.2,
 legend_name='Resident foreign population in %',
 smooth_factor=2
)).add_to(mymap)

title_html = '''
             <h3 align="center" style="font-size:20px"><b>Quantile Median difference in Urban Economic Activities in Berlin</b></h3>
             '''
mymap.get_root().html.add_child(folium.Element(title_html)).add_to(mymap) 

style_function2 = lambda x: {"weight":0.2, 
                            'color':'black',
                           'fillColor':'#000000', 
                           'fillOpacity':0.05}
NIL2 = folium.GeoJson(
    berlinone,
    name='No Activities',
    style_function = style_function2
  
).add_to(mymap)

mymap

In [11]:
style_function = lambda x: {'fillColor': '#ffffff', 
                            'color':'#000000', 
                            'fillOpacity': 0.1, 
                            'weight': 0.1}
highlight_function = lambda x: {'fillColor': '#000000', 
                                'color':'#000000', 
                                'fillOpacity': 0.50, 
                                'weight': 0.1}

tiles = ['cartodbpositron','stamenwatercolor', 'openstreetmap', 'stamenterrain']
for tile in tiles:
    folium.TileLayer(tile).add_to(mymap)



NIL = folium.features.GeoJson(
    berlinhex2,
    style_function=style_function, 
    control=False,
    highlight_function=highlight_function, 
    tooltip=folium.features.GeoJsonTooltip(
        fields=['id_hex','diff_media'],
        aliases=['id: ','Difference: '],
        style=("background-color: white; color: #333333; font-family: arial; font-size: 12px; padding: 10px;") 
    )
)

mymap.add_child(NIL)

mymap.keep_in_front(NIL)
folium.LayerControl(collapsed=False).add_to(mymap)


In [12]:
from branca.element import Template, MacroElement

template = """
{% macro html(this, kwargs) %}

<!doctype html>
<html lang="en">
<head>
  <meta charset="utf-8">
  <meta name="viewport" content="width=device-width, initial-scale=1">
  <title>jQuery UI Draggable - Default functionality</title>
  <link rel="stylesheet" href="//code.jquery.com/ui/1.12.1/themes/base/jquery-ui.css">

  <script src="https://code.jquery.com/jquery-1.12.4.js"></script>
  <script src="https://code.jquery.com/ui/1.12.1/jquery-ui.js"></script>
  
  <script>
  $( function() {
    $( "#maplegend" ).draggable({
                    start: function (event, ui) {
                        $(this).css({
                            right: "auto",
                            top: "auto",
                            bottom: "auto"
                        });
                    }
                });
});

  </script>
</head>
<body>

 
<div id='maplegend' class='maplegend' 
    style='position: absolute; z-index:9999; border:2px solid grey; background-color:rgba(255, 255, 255, 0.8);
     border-radius:6px; padding: 10px; font-size:14px; right: 20px; bottom: 20px;'>
     
<div class='legend-title'>Legend Median difference in quantiles</div>
<div class='legend-scale'>
  <ul class='legend-labels'>
    <li><span style='background:#1a9850;opacity:0.7;'></span>1 Quantile -60  </li>
    <li><span style='background:#66bd63;opacity:0.7;'></span>2 Quantile -59 - 4</li>
    <li><span style='background:#a6d96a;opacity:0.7;'></span>3 Quantile  4  - 72</li>
    <li><span style='background:#ffffbf;opacity:0.7;'></span>4 Quantile  72 - 203 </li>
    <li><span style='background:#fdae61;opacity:0.7;'></span>5 Quantile 203 - 446</li>
    <li><span style='background:#d73027;opacity:0.7;'></span>6 Quantile 446 - 4075 </li>
    <li><span style='background:#4d4d4d;opacity:0.7;'></span>No Economic Activity</li>
  </ul>
</div>
</div>
 
</body>
</html>

<style type='text/css'>
  .maplegend .legend-title {
    text-align: left;
    margin-bottom: 5px;
    font-weight: bold;
    font-size: 90%;
    }
  .maplegend .legend-scale ul {
    margin: 0;
    margin-bottom: 5px;
    padding: 0;
    float: left;
    list-style: none;
    }
  .maplegend .legend-scale ul li {
    font-size: 80%;
    list-style: none;
    margin-left: 0;
    line-height: 18px;
    margin-bottom: 2px;
    }
  .maplegend ul.legend-labels li span {
    display: block;
    float: left;
    height: 16px;
    width: 30px;
    margin-right: 5px;
    margin-left: 0;
    border: 1px solid #999;
    }
  .maplegend .legend-source {
    font-size: 80%;
    color: #777;
    clear: both;
    }
  .maplegend a {
    color: #777;
    }
</style>
{% endmacro %}"""

macro = MacroElement()
macro._template = Template(template)

mymap.get_root().add_child(macro)

mymap

In [13]:
mymap.save('D:/urbban/berlinhex2.html')